Merci à Julien Lavauzelle pour le début de ce TP !

# TP : codage de Huffman et application en cryptographie

### Exercice 1. Utilisation de la bibliothèque.

Dans cet exercice, on va apprendre à utiliser la bibliothèque `binarytree` de python.

In [1]:
from binarytree import *

La fonction `Node(x)` permet de créer un arbre constitué d'une feuille, dont l'étiquette est `x`.

**Question 1.-** Créer un arbre `T` constitué d'une feuille, dont l'étiquette est le caractère `a`. Puis, afficher cet arbre avec la commande `print`.

Pour créer un arbre plus complexe, l'idée est d'assigner des descendants aux noeuds de l'arbre. Les descendants droit et gauche d'un noeud doivent eux-même être des noeuds. Par exemple, si `T` est un noeud et `G` est un autre noeud, alors on peut demander à ce que `G` soit le descendant à gauche de `T` en écrivant `T.left = G`. 

**Question 2.-** Créer un arbre binaire de hauteur $1$, dont la racine a pour étiquette `0`, la feuille gauche a pour étiquette `a` et la feuille droite a pour étiquette `b`. Puis, afficher cet arbre.

On accède à l'étiquette d'un noeud `T` grâce à l'attribut `T.value`

**Question 3.-** Modifier l'arbre précédent pour que l'étiquette de la racine soit le caractère "x".

**Question 4.-** À l'aide d'une boucle, créer l'arbre suivant :
```
              0
             /
            1
           /
          2
         /
        3
       /
      4
     /
    5
   /
  6
 /
7
```

## Exercice 2. Code de Huffman

Pour rappel, l'algorithme de Huffman fonctionne de la sorte. Il prend en entrée une distribution $p = (p(x_1), \dots, p(x_n))$, et calcule un arbre binaire de la manière suivante.
  1. On initialise une séquence `D` d'arbres-feuilles, dont les étiquettes sont les symboles $(x_1, \dots, x_n)$
  2. Tant que la séquence contient au moins deux arbres :
    1. on trouve dans la distribution $p$ les deux valeurs minimales $p(x_i)$ et $p(x_j)$
    2. on identifie dans `D` les deux arbres correspondants $T_i$ et $T_j$
    3. on retire $p(x_i)$ et $p(x_j)$ de $p$, et on lui rajoute la probabilité formée de la somme de ces probabilités 
    4. on retire les arbres $T_i$ et $T_j$ de `D`, et on lui rajoute l'arbre formé de la réunion de ces deux sous-arbres
  3. On retourne de dernier arbre de la séquence
  
Pour implanter l'algorithme, nous allons utiliser une structure de dictionnaire pour représenter à la fois les "séquences d'arbres" et les distributions. Le dictionnaire `D` correspondant aura comme clés des couples $(x, p(x))$, où $x$ représente la concaténation des symboles dans l'arbre, et $p(x)$ la somme des probabilités correspondantes. La valeur `D[k]` de la clé `k = (x, p(x))` sera l'arbre correspondant.

Pour bien se le représenter, commençons par initialiser ce dictionnaire.

**Question 1.-** Étant donnée une distribution $p$ stockée sous forme de dictionnaire, construire le dictionnaire initial `D`, dont les clés sont les couples $(x, p(x))$ et dont les valeurs sont les arbres-feuilles d'étiquette $x$.

*Exemple : si la source a pour alphabet $\{ a, b, c, d \}$ et pour distribution associée $p = (0.4, 0.3, 0.2, 0.1)$, alors on doit obtenir le dictionnaire :*
```
D = {('a', 0.4): Node(a), ('b', 0.3): Node(b), ('c', 0.2): Node(c), ('d', 0.1): Node(d)}
```

In [2]:
p = { "a":0.4, "b":0.3, "c":0.2, "d":0.1 }

Dans le dictionnaire `D`, on peut obtenir la clé $(x, p(x))$ correspondant à la probabilité la plus faible en écrivant :
```
min(D, key=lambda y:y[1])
```

**Question 2.-** Vérifier cela en exécutant le code ci-dessus.

Étant donné un dictionnaire d'arbres `D` sous la forme présentée ci-dessus, on souhaite effectuer une étape de boucle de l'algorithme de Huffman. À savoir :
 1. stocker dans `T1` et `T2` les arbres de `D` dont les probabilités associées sont les plus petites
 2. créer l'arbre `T` dont l'étiquette est la concaténation des étiquettes de `T1` et `T2` (par exemple séparée d'un "|"), et dont le sous-arbre gauche est `T1` et le sous-arbre droit est `T2`  
 3. retirer `T1` et `T2` de `D`, et ajouter `T` dans `D` (avec la clé égale au couple formé de son étiquette concaténée et de sa probabilité "somme")
 
**Question 3.-** On donne le code suivant, qui exécute cette étape sur le dictionnaire `D` créé précédemment. Le lire et le comprendre.

In [ ]:
# on cherche l'arbre dont la proba associée est la plus petite
k1 = min(D, key=lambda y:y[1])   # calcul de la clé correspondant à la proba minimale
T1 = D[k1]                       # obtention de l'arbre correspondant (dans le dictionnaire D)
p = k1[1]                        # obtention de la probabilité correspondante
D.pop(k1)                        # on retire cet arbre du dictionnaire

# puis on réitère pour la seconde probabilité la plus petite
k2 = min(D, key=lambda y:y[1])   
T2 = D[k2]
p += k2[1]                       # ici, on somme avec la probabilité précédente
D.pop(k2)

# enfin on contruit l'arbre "concaténé"
T = Node(T1.value + "|" + T2.value)   # T1.value + "|" + T2.value correspond à la valeur à assigner
T.left = T1                           # on créée le fils gauche
T.right = T2                          #          le fils droit
D[tuple([T.value, p])] = T            # puis on ajoute l'arbre nouvellement créé dans le dictionnaire

print(D)

**Question 4.-** On donne le code suivant qui construit un arbre de Huffman étant donné une distribution de probabilité $p$. Le lire et le comprendre.

In [3]:
def huffman(p):
    
    # On associe à chaque symbole un "arbre-feuille"
    # dans un dictionnaire
    D = { tuple([x, p[x]]): Node(x) for x in p }

    # On fusionne les arbres de manière itérative,
    # dans une boucle while
    while len(D) != 1:

        # on cherche les deux arbres à fusionner
        new_p = 0                         # la nouvelle proba = 0
        m1 = min(D, key=lambda y: y[1])   # symbole de proba min
        T1 = D[m1]                        # arbre associé
        new_p += m1[1]                    # mise à jour de la nouvelle proba
        D.pop(m1)                         # on le retire du dictionnaire
        m2 = min(D, key=lambda y: y[1])   # 2nd symbole de proba min
        T2 = D[m2]                        # 2nd arbre associé
        new_p += m2[1]                    # mise à jour de la nouvelle proba
        D.pop(m2)                         # on le retire du dictionnaire

        # on crée la fusion des deux arbres sélectionnés
        T = Node(T1.value + "|" + T2.value)                      # la racine
        T.left = T1                       # descendant gauche = T1
        T.right = T2                      # descendant droit = T2
        
        # on place cet arbre fusionné dans le dictionnaire
        D[tuple([T.value, new_p])] = T

    return D[list(D.keys())[0]]

**Question 5.-** Tester l'algorithme sur la distribution :
```
p = { "a":0.4, "b":0.3, "c":0.2, "d":0.1 }
```
Vous devriez obtenir :
```
  a|b|d|c____
 /           \
a           b|d|c___
           /        \
          b         d|c
                   /   \
                  d     c
```

**Question 6.-** Écrire une fonction qui, étant donné un arbre binaire, construit un dictionnaire représentant le code associé : les clés du dictionnaire sont les lettres, et la valeur associée à une clé est le mot de code correspondant.

**Question 7.-** Écrire une fonction qui, étant donné une distribution de probabilités et un mot, renvoie le résultat du codage de ce mot par le code de Huffman associé à la distribution donnée.

**Question 8.-** Tester cette fonction sur la distribution de la question 5 et le mot "abdbbaac".

**Question 9.-** Écrire une fonction qui, étant donné un arbre de Huffman $T$ et une chaîne de bits $m$, décode $m$ en supposant qu'elle est le codage d'une chaîne de caractères par le codage associé à l'arbre $T$.

**Question 10.-** Tester cette fonction sur le résultat de la question 8.

### Exercice 3 : Un cryptosystème à base d'arbres de Huffman

En 2022, Gross, Klein, Opalinsky, Revivo et Shapira ont proposé un système de chiffrement symétrique de messages utilisant le code de Huffman. Cet exercice en étudie une version simplifiée. Le principe est le suivant. Soit $A$ un alphabet, et $\mathcal{P}$ une distribution de probabilités sur $A$. Soit $T$ un arbre de Huffman associé à $\mathcal{P}$. Alice et Bob possèdent tous les deux une clé secrète $\{ v_1,\dots,v_k\}$ où les $v_i\in \{0,1\}^\star$ désignent des noeuds de l'arbre $T$. On se donne une transformation $\sigma$ (voir ci-dessous).

Alice souhaite chiffer un message $m=x_1\dots x_n\in A^n$. Pour $i=1,\dots,n$, ell met à jour $T$ selon la règle suivante : pour $i=1,\dots,k$, elle applique la transformation $\sigma$ au sous-arbre de $T$ de racine $v_i$. Elle code $x_i$ selon l'arbre $T$, puis applique la même procédure à $x_{i+1}\dots x_n$.

**Question 1.-** La première transformation possible est $\mathsf{MIRROR}$. Elle prend un arbre binaire $T$ et lui fait correspondre son arbre miroir $\mathsf{MIRROR}(T)$ défini de la façon suivante : $x$ et un fils droit de $y$ dans $\mathsf{MIRROR}(T)$ si et seulement si $x$ est un fils gauche de $y$ dans $T$. Écrire une fonction qui à un arbre $T$ et à un noeud $v$ associe l'arbre obtenu en appliquant $\mathsf{MIRROR}$ au sous-arbre de $T$ de racine $v$.

**Question 2.-** La deuxième transformation possible est $\mathsf{SWAP}$. Elle prend un arbre $T$ et lui fait correspondre l'arbre $\mathsf{SWAP}(T)$, qui est obtenu en échangent les sous-arbres gauche et droit de $T$. Écrire une fonction qui à un arbre $T$ et à un noeud $v$ associe l'arbre obtenu en appliquant $\mathsf{SWAP}$ au sous-arbre de $T$ de racine $v$.

**Question 3.-** Écrire une fonction qui à un arbre $T$ et une liste $[v_1,\dots,v_k]$ de noeuds de $T$ associe l'arbre obtenu en appliquant $\mathsf{MIRROR}(-,v_k)\circ\dots\circ \mathsf{MIRROR}(-,v_1)$ à $T$. Faire de même avec l'opération $\mathsf{SWAP}$.

**Question 4.-** Écrire une fonction qui, étant donné un arbre de Huffman $T$, une clé secrète $\{ v_1,\dots,v_k\}$ et un mot $m\in A^\star$, chiffre $m$ selon l'algorithme décrit ci-dessus.

**Question 5.-** Pour déchiffrer un chiffré $c=y_1\dots y_s\in \{0,1\}^\star$, Bob décode le début du mot $c$ en utilisant l'arbre de Huffman de départ $T$, puis lui applique les mêmes transformations qu'Alice, puis recommence sur la partie restante de $c$. Écrire une fonction qui réalise ce déchiffrement.

**Question 6.-** Proposer une attaque sur ce système de chiffrement. On pourra supposer qu'on peut demander à Alice de chiffrer des messages choisis et voir les chiffrés obtenus.